In [1]:
import numpy as np
import matplotlib.pyplot as plt
import fathon
from fathon import fathonUtils as fu
import pandas as pd
import seaborn as sns
import os
import matplotlib.pyplot as plt
import statsmodels.api as sm
import pickle
plt.rcParams['font.sans-serif'] = 'Helvetica'
plt.rcParams['axes.edgecolor']='#333F4B'
plt.rcParams['axes.linewidth']=0.8
plt.rcParams['xtick.color']='#333F4B'
plt.rcParams['ytick.color']='#333F4B'
import itertools
from collections import defaultdict
import pandas as pd
import freqopttest.util as util
import freqopttest.data as data
import freqopttest.kernel as kernel
import freqopttest.tst as tst

import freqopttest.glo as glo
import sys
import time
import itertools

In [2]:
def generate_column_pairs(num_columns):
    """
    Generates pairs of columns for sliding window analysis.

    Args:
        num_columns (int): The total number of columns.

    Yields:
        tuple: A tuple containing the start index, end index, and shift for a pair of columns.
               The start and end indices define the column pair, and the shift indicates the distance
               by which one column is shifted with respect to the other.
    """
    for window in range(1, num_columns):
        for shift in range(1, num_columns - window + 1):
            for start_point, end_point in itertools.combinations(range(num_columns), 2):
                if end_point - start_point == window:
                    yield start_point, end_point, shift


def create_kgauss(sigma2, default_sigma2=None):
    """
    Create a KGauss instance with the given sigma2 value, or use the default_sigma2 value if provided.

    :param sigma2: float, the sigma2 value to use for creating the KGauss instance.
    :param default_sigma2: float, optional, the default sigma2 value to use if the provided sigma2 is invalid.
    :return: KGauss, the created KGauss instance.
    :raise ValueError: if both sigma2 and default_sigma2 are invalid.
    """
    if sigma2 > 0:
        return kernel.KGauss(sigma2)
    elif default_sigma2 is not None and default_sigma2 > 0:
        print("Using default sigma2 value:", default_sigma2)
        return kernel.KGauss(default_sigma2)
    else:
        raise ValueError("Both sigma2 and default_sigma2 are invalid. Please provide a positive value for either.")


def simulate_null_spectral(weights, n_simulate=1000, seed=275):
    """
    weights: chi-square weights (for the infinite weigted sum of chi squares)
    Return the values of MMD^2 (NOT n*MMD^2) simulated from the null distribution by
    the spectral method.
    """
    # draw at most block_size values at a time
    block_size = 400
    D = weights.shape[0]  # len(weights)
    mmds = np.zeros(n_simulate)
    from_ind = 0

    with util.NumpySeedContext(seed=seed):
        while from_ind < n_simulate:
            to_draw = min(block_size, n_simulate - from_ind)
            # draw chi^2 random variables.
            chi2 = np.random.randn(D, to_draw) ** 2
            # an array of length to_draw
            sim_mmds = 2.0 * weights.dot(chi2 - 1.0)
            # store
            end_ind = from_ind + to_draw
            mmds[from_ind:end_ind] = sim_mmds
            from_ind = end_ind
    return mmds

def chi_square_weights_H0(k, X):
    """
    Return a numpy array of the weights to be used as the weights in the
    weighted sum of chi-squares for the null distribution of MMD^2.
    - k: a Kernel
    - X: n x d number array of n data points
    """
    try:
        n = X.shape[0]
        # Gram matrix
        K = k.eval(X, X)
        # centring matrix. Not the most efficient way.
        H = np.eye(n) - np.ones((n, n)) / float(n)
        HKH = H.dot(K).dot(H)
        # https://docs.scipy.org/doc/numpy-1.14.0/reference/generated/numpy.linalg.eigvals.html
        evals = np.linalg.eigvals(HKH)
        evals = np.real(evals)
        # sort in decreasing order
        evals = -np.sort(-evals)
        weights = evals / float(n) ** 2
        return weights
    except np.linalg.LinAlgError as e:
        print("LinAlgError:", str(e))
        return np.array([])  # Return an empty array or any other appropriate value

### Filepaths and Files ###

In [3]:
reconLOBs = '/media/ak/Data/InterestRateFuturesData/ReconstructedLOB'
figuresLocation = '/home/ak/Documents/Research/Papers/StylisedFactsPaper/figures'
symbols = sorted(os.listdir(reconLOBs))
symbolFolders = [os.path.join(reconLOBs, symbol) for symbol in symbols]

# os.listdir('/media/ak/Data1/InterestRateFuturesData/')
directory = 'OrderBookImbalance'
path = os.path.join(reconLOBs, directory, 'extremes', )
# Assuming you have a list of file paths
obiFiles = os.listdir(path)
file_paths = [os.path.join(path, obiFiles[i]) for i in range(7)]
obimfdfaPath= '/media/ak/Data/InterestRateFuturesData/ReconstructedLOB/OrderBookImbalance/OBIMFDFA'

In [7]:
symbols = list(data_dict.keys())
print(symbols)

['DU1', 'FB1', 'JB1', 'OE1', 'FV1', 'G', 'KE1', 'RX1', 'US1', 'XM1', 'YM1']


In [9]:


# Keys of interest
mfdfakeys = ['orderBookImbalance', 'n', 'F', 'list_H', 'list_H_intercept', 'tau', 'alpha', 'mfSpect', 'qs']

# Initialize a nested defaultdict
data_dict = defaultdict(lambda: defaultdict(dict))

files = os.listdir(obimfdfaPath)
files = [f for f in files if str('_data') not in f]

# Iterate over files and aggregate data
for filename in files:
    symbol = filename.split("_")[0]  # Extracting symbol from filename
#     print(symbol)
    file_path = os.path.join(obimfdfaPath, filename)
    unpickledData = pd.read_pickle(file_path)  # Assuming data is a dict of dicts
    keys = list(unpickledData.keys())
# # #     # Iterate over each key and index
    for idx in keys:
        for key in mfdfakeys:
            data_dict[symbol][key][idx] = unpickledData[idx][key]

# Assuming `a_args` and `second_arg` are defined
mmd_train_test_results = defaultdict(dict)
a_args = [1, 2, 3]  # Example values
second_arg = [1, 4, 5, 6, 8, 10]  # Example values

c = list(itertools.product(a_args, second_arg))
symbol = 'DU1'
mfdfakey = 'list_H'
choice_dataframe = pd.DataFrame.from_dict( data_dict[str(symbol)][str(mfdfakey)] )
# Replace 'len' with a different variable name, like 'length'
length = choice_dataframe.shape[1]  # This should be set to your actual length value

for shift, window in c:
    for start_point in range(0, (length - window - shift)):
        end_point = start_point + shift
        X = np.array(choice_dataframe.iloc[:, start_point:end_point])
        Y = np.array(choice_dataframe.iloc[:, end_point + shift:end_point + 2 * shift])
        Z = np.array(choice_dataframe.iloc[:, start_point + window:end_point + window])
        try:
            tr_data = data.TSTData(X, Y)
            test_data_one = data.TSTData(X, Z)  # data to train the model
            test_data_two = data.TSTData(Y, Z)
            # training dictionary results
            tr, te = tr_data.split_tr_te(tr_proportion=0.95, seed=10)  # is this necessary?!

            xtr, ytr = tr.xy()
            xytr = tr.stack_xy()
            sig2 = util.meddistance(xytr, subsample=1000)
            k = kernel.KGauss(sig2)
            mean, var = tst.QuadMMDTest.h1_mean_var(xtr, ytr, k, is_var_computed=True)
            Kx = k.eval(xtr, xtr)
            Ky = k.eval(ytr, ytr)
            Kxy = k.eval(xtr, ytr)
            mean_gram, var_gram = tst.QuadMMDTest.h1_mean_var_gram(Kx, Ky, Kxy, k, True)
            chi2_weights = chi_square_weights_H0(k, xytr)
            sim_mmds = simulate_null_spectral(chi2_weights, n_simulate=2000)
            # choose the best parameter and perform a test with permutations
            med = util.meddistance(tr.stack_xy(), 1000)
            list_gwidth = np.hstack(((med ** 2) * (2.0 ** np.linspace(-4, 4, 20))))
            list_gwidth.sort()
            list_kernels = [kernel.KGauss(gw2) for gw2 in list_gwidth]

            # grid search to choose the best Gaussian width
            besti, powers = tst.QuadMMDTest.grid_search_kernel(tr, list_kernels, alpha=0.05)
            # perform test
            best_ker = list_kernels[besti]
            mmd_train_test_results[start_point]['perm_mmds1'] = tst.QuadMMDTest.permutation_list_mmd2(xtr, ytr, k,
                                                                                                      n_permute=2000)
            mmd_train_test_results[start_point]['chi2_weights'] = chi2_weights
            mmd_train_test_results[start_point]['sim_mmds'] = sim_mmds
            mmd_train_test_results[start_point]['sig2'] = sig2
            mmd_train_test_results[start_point]['Kxy'] = k.eval(xtr, ytr)
            mmd_train_test_results[start_point]['mean'] = mean
            mmd_train_test_results[start_point]['var'] = var
            mmd_train_test_results[start_point]['Kxx'] = k.eval(xtr, xtr)
            mmd_train_test_results[start_point]['Kyy'] = k.eval(ytr, ytr)
            mmd_train_test_results[start_point]['mean_gram'] = mean_gram
            mmd_train_test_results[start_point]['var_gram'] = var_gram
            mmd_train_test_results[start_point]['med'] = util.meddistance(tr.stack_xy(), 1000)
            mmd_train_test_results[start_point]['list_gwidth'] = list_gwidth.sort()
            mmd_train_test_results[start_point]['list_kernels'] = list_kernels
            mmd_train_test_results[start_point]['besti'] = besti
            mmd_train_test_results[start_point]['powers'] = powers
            mmd_train_test_results[start_point]['best_ker'] = best_ker

            alpha = 0.05
            mmd_test = tst.QuadMMDTest(best_ker, n_permute=2000, alpha=alpha)
            mmd_train_test_results[start_point]['XZ_test'] = mmd_test.perform_test(test_data_one)
            mmd_train_test_results[start_point]['YZ_test'] = mmd_test.perform_test(test_data_two)
        except ValueError:
            pass
        
        pickle_out_dict_one = os.path.join(obimfdfaPath, "".join(
                (str(symbol) + "_" + str(mfdfakey) + "_shift_" + str(shift) + "_wind_" + str(window) + "_" + str(
                    'OBI_quad_MMD_test') + ".pkl")))
        pickle.dump(mmd_train_test_results, open(pickle_out_dict_one, 'wb'), protocol=pickle.HIGHEST_PROTOCOL)



    


(1/20) KGauss(w2=0.006): mmd2: 0.0239, var: 6.64e-07, power obj: 0.755359, took: 0.0002713203430175781
(2/20) KGauss(w2=0.008): mmd2: 0.0232, var: 7.81e-06, power obj: 0.729468, took: 0.0002989768981933594
(3/20) KGauss(w2=0.010): mmd2: 0.0219, var: 5.28e-06, power obj: 0.689717, took: 0.0003020763397216797
(4/20) KGauss(w2=0.014): mmd2: 0.0202, var: 3.48e-06, power obj: 0.638206, took: 0.0002963542938232422
(5/20) KGauss(w2=0.018): mmd2: 0.0183, var: 2.25e-06, power obj: 0.579569, took: 0.00033926963806152344
(6/20) KGauss(w2=0.024): mmd2: 0.0164, var: 1.41e-06, power obj: 0.516689, took: 0.00028443336486816406
(7/20) KGauss(w2=0.033): mmd2: 0.0143, var: 8.62e-07, power obj: 0.4516, took: 0.0002906322479248047
(8/20) KGauss(w2=0.044): mmd2: 0.0122, var: 5.2e-07, power obj: 0.386353, took: 0.0002887248992919922
(9/20) KGauss(w2=0.058): mmd2: 0.0102, var: 3.12e-07, power obj: 0.323119, took: 0.0002903938293457031
(10/20) KGauss(w2=0.078): mmd2: 0.00834, var: 1.87e-07, power obj: 0.26374

(1/20) KGauss(w2=0.002): mmd2: 0.0874, var: 0.00105, power obj: 1.93285, took: 0.0002853870391845703
(2/20) KGauss(w2=0.003): mmd2: 0.0967, var: 0.00122, power obj: 2.05454, took: 0.0005252361297607422
(3/20) KGauss(w2=0.004): mmd2: 0.106, var: 0.00141, power obj: 2.1646, took: 0.00041794776916503906
(4/20) KGauss(w2=0.005): mmd2: 0.116, var: 0.00163, power obj: 2.2605, took: 0.0003895759582519531
(5/20) KGauss(w2=0.007): mmd2: 0.126, var: 0.00188, power obj: 2.34088, took: 0.00034499168395996094
(6/20) KGauss(w2=0.009): mmd2: 0.135, var: 0.00215, power obj: 2.40644, took: 0.00039076805114746094
(7/20) KGauss(w2=0.012): mmd2: 0.144, var: 0.00241, power obj: 2.45865, took: 0.00034999847412109375
(8/20) KGauss(w2=0.016): mmd2: 0.15, var: 0.00262, power obj: 2.49822, took: 0.0003509521484375
(9/20) KGauss(w2=0.022): mmd2: 0.154, var: 0.00273, power obj: 2.52587, took: 0.0003528594970703125
(10/20) KGauss(w2=0.029): mmd2: 0.154, var: 0.00267, power obj: 2.54262, took: 0.0003457069396972656

(1/20) KGauss(w2=0.004): mmd2: 0.0505, var: 0.000715, power obj: 1.22039, took: 0.0003724098205566406
(2/20) KGauss(w2=0.005): mmd2: 0.0559, var: 0.000805, power obj: 1.31507, took: 0.0005807876586914062
(3/20) KGauss(w2=0.007): mmd2: 0.0609, var: 0.000885, power obj: 1.40268, took: 0.0004448890686035156
(4/20) KGauss(w2=0.010): mmd2: 0.0654, var: 0.00095, power obj: 1.48107, took: 0.0004584789276123047
(5/20) KGauss(w2=0.013): mmd2: 0.0692, var: 0.000997, power obj: 1.54863, took: 0.0004374980926513672
(6/20) KGauss(w2=0.017): mmd2: 0.0723, var: 0.00103, power obj: 1.60431, took: 0.0004315376281738281
(7/20) KGauss(w2=0.023): mmd2: 0.0746, var: 0.00105, power obj: 1.64742, took: 0.00035834312438964844
(8/20) KGauss(w2=0.031): mmd2: 0.0765, var: 0.00108, power obj: 1.67683, took: 0.00040030479431152344
(9/20) KGauss(w2=0.041): mmd2: 0.0779, var: 0.00113, power obj: 1.69002, took: 0.0003972053527832031
(10/20) KGauss(w2=0.055): mmd2: 0.079, var: 0.0012, power obj: 1.68455, took: 0.00036

(1/20) KGauss(w2=0.004): mmd2: 0.139, var: 0.00161, power obj: 2.71753, took: 0.00028514862060546875
(2/20) KGauss(w2=0.005): mmd2: 0.154, var: 0.0019, power obj: 2.85717, took: 0.0005118846893310547
(3/20) KGauss(w2=0.006): mmd2: 0.167, var: 0.00215, power obj: 2.97907, took: 0.0003457069396972656
(4/20) KGauss(w2=0.009): mmd2: 0.179, var: 0.00236, power obj: 3.08285, took: 0.00033664703369140625
(5/20) KGauss(w2=0.012): mmd2: 0.186, var: 0.00246, power obj: 3.16631, took: 0.00033020973205566406
(6/20) KGauss(w2=0.015): mmd2: 0.19, var: 0.00246, power obj: 3.22459, took: 0.0003299713134765625
(7/20) KGauss(w2=0.021): mmd2: 0.187, var: 0.00232, power obj: 3.24956, took: 0.0003299713134765625
(8/20) KGauss(w2=0.028): mmd2: 0.18, var: 0.00209, power obj: 3.2282, took: 0.00032019615173339844
(9/20) KGauss(w2=0.037): mmd2: 0.167, var: 0.00182, power obj: 3.1389, took: 0.0003209114074707031
(10/20) KGauss(w2=0.050): mmd2: 0.15, var: 0.0016, power obj: 2.95353, took: 0.00032067298889160156
(

(1/20) KGauss(w2=0.005): mmd2: 0.0765, var: 0.000934, power obj: 1.74054, took: 0.00028634071350097656
(2/20) KGauss(w2=0.006): mmd2: 0.0811, var: 0.001, power obj: 1.81157, took: 0.0004620552062988281
(3/20) KGauss(w2=0.009): mmd2: 0.0846, var: 0.00106, power obj: 1.86655, took: 0.00030159950256347656
(4/20) KGauss(w2=0.011): mmd2: 0.087, var: 0.00108, power obj: 1.90715, took: 0.0003120899200439453
(5/20) KGauss(w2=0.015): mmd2: 0.0881, var: 0.00108, power obj: 1.93451, took: 0.0003025531768798828
(6/20) KGauss(w2=0.021): mmd2: 0.0878, var: 0.00103, power obj: 1.94764, took: 0.0002932548522949219
(7/20) KGauss(w2=0.027): mmd2: 0.0859, var: 0.000954, power obj: 1.94227, took: 0.00029277801513671875
(8/20) KGauss(w2=0.037): mmd2: 0.0823, var: 0.000853, power obj: 1.9114, took: 0.00028967857360839844
(9/20) KGauss(w2=0.049): mmd2: 0.0772, var: 0.00075, power obj: 1.84639, took: 0.0002961158752441406
(10/20) KGauss(w2=0.066): mmd2: 0.0712, var: 0.000677, power obj: 1.73857, took: 0.00031

...

(1/20) KGauss(w2=0.017): mmd2: 0.285, var: 0.00047, power obj: 7.42465, took: 0.0003230571746826172
(2/20) KGauss(w2=0.023): mmd2: 0.293, var: 0.000335, power obj: 8.02428, took: 0.000308990478515625
(3/20) KGauss(w2=0.031): mmd2: 0.294, var: 0.000179, power obj: 8.55436, took: 0.0003497600555419922
(4/20) KGauss(w2=0.041): mmd2: 0.287, var: 4.03e-05, power obj: 8.90239, took: 0.0003376007080078125
(5/20) KGauss(w2=0.055): mmd2: 0.275, var: 0.000125, power obj: 8.19523, took: 0.0003361701965332031
(6/20) KGauss(w2=0.073): mmd2: 0.259, var: 0.000114, power obj: 7.74686, took: 0.00032973289489746094
(7/20) KGauss(w2=0.098): mmd2: 0.24, var: 0.000103, power obj: 7.2209, took: 0.0003299713134765625
(8/20) KGauss(w2=0.131): mmd2: 0.22, var: 9.19e-05, power obj: 6.65635, took: 0.0003304481506347656
(9/20) KGauss(w2=0.176): mmd2: 0.2, var: 7.91e-05, power obj: 6.07913, took: 0.0003285408020019531
(10/20) KGauss(w2=0.235): mmd2: 0.18, var: 6.52e-05, power obj: 5.50376, took: 0.0003395080566406

(1/20) KGauss(w2=0.011): mmd2: 0.253, var: 0.000492, power obj: 6.54106, took: 0.00040340423583984375
(2/20) KGauss(w2=0.014): mmd2: 0.257, var: 0.000378, power obj: 6.92181, took: 0.0005431175231933594
(3/20) KGauss(w2=0.019): mmd2: 0.254, var: 0.000237, power obj: 7.21109, took: 0.0004985332489013672
(4/20) KGauss(w2=0.025): mmd2: 0.243, var: 9.46e-05, power obj: 7.35569, took: 0.0004520416259765625
(5/20) KGauss(w2=0.034): mmd2: 0.228, var: 8.54e-05, power obj: 6.91069, took: 0.0003314018249511719
(6/20) KGauss(w2=0.045): mmd2: 0.208, var: 6.91e-05, power obj: 6.36786, took: 0.0003933906555175781
(7/20) KGauss(w2=0.061): mmd2: 0.187, var: 5.39e-05, power obj: 5.74898, took: 0.0004706382751464844
(8/20) KGauss(w2=0.081): mmd2: 0.164, var: 4.06e-05, power obj: 5.09876, took: 0.0003840923309326172
(9/20) KGauss(w2=0.109): mmd2: 0.143, var: 2.96e-05, power obj: 4.45469, took: 0.0003750324249267578
(10/20) KGauss(w2=0.145): mmd2: 0.123, var: 2.09e-05, power obj: 3.84371, took: 0.00037384

(1/20) KGauss(w2=0.009): mmd2: 0.0395, var: 2.52e-05, power obj: 1.23237, took: 0.00031113624572753906
(2/20) KGauss(w2=0.012): mmd2: 0.0381, var: 2.73e-05, power obj: 1.1884, took: 0.00048160552978515625
(3/20) KGauss(w2=0.016): mmd2: 0.0365, var: 2.81e-05, power obj: 1.13969, took: 0.00034046173095703125
(4/20) KGauss(w2=0.021): mmd2: 0.0349, var: 2.72e-05, power obj: 1.08815, took: 0.0003337860107421875
(5/20) KGauss(w2=0.028): mmd2: 0.0331, var: 2.48e-05, power obj: 1.03374, took: 0.0003325939178466797
(6/20) KGauss(w2=0.038): mmd2: 0.0312, var: 2.12e-05, power obj: 0.975361, took: 0.0003445148468017578
(7/20) KGauss(w2=0.051): mmd2: 0.0291, var: 1.71e-05, power obj: 0.912233, took: 0.00033020973205566406
(8/20) KGauss(w2=0.068): mmd2: 0.0269, var: 1.31e-05, power obj: 0.844976, took: 0.00032591819763183594
(9/20) KGauss(w2=0.092): mmd2: 0.0246, var: 9.6e-06, power obj: 0.775491, took: 0.0003273487091064453
(10/20) KGauss(w2=0.123): mmd2: 0.0224, var: 6.75e-06, power obj: 0.705759,

(1/20) KGauss(w2=0.008): mmd2: 0.113, var: 6.45e-05, power obj: 3.46765, took: 0.0003218650817871094
(2/20) KGauss(w2=0.011): mmd2: 0.113, var: 7.11e-05, power obj: 3.45805, took: 0.0004875659942626953
(3/20) KGauss(w2=0.015): mmd2: 0.112, var: 8.56e-05, power obj: 3.40163, took: 0.0003590583801269531
(4/20) KGauss(w2=0.020): mmd2: 0.11, var: 0.000102, power obj: 3.30409, took: 0.00034618377685546875
(5/20) KGauss(w2=0.026): mmd2: 0.106, var: 0.000111, power obj: 3.17653, took: 0.00038051605224609375
(6/20) KGauss(w2=0.035): mmd2: 0.101, var: 0.000103, power obj: 3.02903, took: 0.0003418922424316406
(7/20) KGauss(w2=0.047): mmd2: 0.0939, var: 7.41e-05, power obj: 2.86595, took: 0.0003447532653808594
(8/20) KGauss(w2=0.063): mmd2: 0.0861, var: 2.75e-05, power obj: 2.68609, took: 0.00034117698669433594
(9/20) KGauss(w2=0.084): mmd2: 0.0775, var: 2.6e-05, power obj: 2.41836, took: 0.0003387928009033203
(10/20) KGauss(w2=0.113): mmd2: 0.0684, var: 1.91e-05, power obj: 2.14374, took: 0.0003

(1/20) KGauss(w2=0.007): mmd2: 0.159, var: 0.000338, power obj: 4.34582, took: 0.0003027915954589844
(2/20) KGauss(w2=0.010): mmd2: 0.151, var: 0.000261, power obj: 4.25883, took: 0.0004723072052001953
(3/20) KGauss(w2=0.013): mmd2: 0.141, var: 0.00018, power obj: 4.0934, took: 0.00034546852111816406
(4/20) KGauss(w2=0.017): mmd2: 0.128, var: 0.000105, power obj: 3.85976, took: 0.0003387928009033203
(5/20) KGauss(w2=0.023): mmd2: 0.115, var: 3.83e-05, power obj: 3.57673, took: 0.00033402442932128906
(6/20) KGauss(w2=0.031): mmd2: 0.102, var: 3.09e-05, power obj: 3.18374, took: 0.000324249267578125
(7/20) KGauss(w2=0.041): mmd2: 0.0898, var: 2.34e-05, power obj: 2.80556, took: 0.000362396240234375
(8/20) KGauss(w2=0.055): mmd2: 0.0782, var: 1.72e-05, power obj: 2.45072, took: 0.00033783912658691406
(9/20) KGauss(w2=0.073): mmd2: 0.0676, var: 1.22e-05, power obj: 2.12586, took: 0.00033164024353027344
(10/20) KGauss(w2=0.098): mmd2: 0.0583, var: 8.39e-06, power obj: 1.83487, took: 0.00032